# Load Libraries

In [127]:
import numpy as np
import pandas as pd

import torch
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt

PATH='data/'

In [128]:
import random
random.seed(5)

# Load Data

In [129]:
benutzergruppen_df = pd.read_csv(f'{PATH}benutzergruppen_df.csv', low_memory=False)

Ich nehme die 15 Variablen, die laut Random Forest die wichtigsten sein sollen (bei random Forest accuracy von knapp 60%)

In [130]:
benutzergruppen_df = benutzergruppen_df[['Clusternumber', 'age', 'desktop_dev_rnk','mobile_dev_rnk', 'tablet_dev_rnk', 'desktop_temp_rnk', 'mobile_temp_rnk', 'app_temp_rnk', 'intensive_rnk', 'after_rnk', 'insp_rnk', 'schwach_rnk', 'sehr_intensive_rnk', 'produktbez_rnk', 'fokus_rnk', 'aff_rnk', 'seo_br_rnk', 'mail_rnk', 'sonstige_rnk', 'sma_rnk', 'ret_rnk', 'sem_br_rnk', 'sem_rnk', 'seo_rnk', 'psm_rnk']]
benutzergruppen_df.head()

Clusternumber   age  desktop_dev_rnk  mobile_dev_rnk  tablet_dev_rnk  \
0              1   NaN                1               4               4   
1              4  24.0                2               1               4   
2              2  28.0                1               2               4   
3              1  49.0                1               4               4   
4              1  40.0                1               2               4   

   desktop_temp_rnk  mobile_temp_rnk  app_temp_rnk  intensive_rnk  after_rnk  \
0                 1                4             4              5          8   
1                 2                4             1              6          2   
2                 1                3             2              3          1   
3                 1                4             4              5          7   
4                 1                2             4              8          8   

    ...     aff_rnk  seo_br_rnk  mail_rnk  sonstige_rnk  sma_rnk  ret_rnk  \
0   ...          11          11         1             2       11       11   
1   ...          11          11         2             1        4       11   
2   ...          11          11         4             1       11        6   
3   ...           2           6         1             6       11        4   
4   ...          11          11         2             1       11       11   

   sem_br_rnk  sem_rnk  seo_rnk  psm_rnk  
0          11       11       11       11  
1           4        4       11       11  
2           6       11        2        5  
3          11       11       11       11  
4          11       11       11       11  

[5 rows x 25 columns]

# Data preparation

## Helper Functions

In [131]:
def proc_df(df, y_fld=None, skip_flds=None, ignore_flds=None, do_scale=False, na_dict=None,
            preproc_fn=None, max_n_cat=None, subset=None, mapper=None):

    if not ignore_flds: ignore_flds=[]
    if not skip_flds: skip_flds=[]
    if subset: df = get_sample(df,subset)
    ignored_flds = df.loc[:, ignore_flds]
    df.drop(ignore_flds, axis=1, inplace=True)
    df = df.copy()
    if preproc_fn: preproc_fn(df)
    if y_fld is None: y = None
    else:
        if not is_numeric_dtype(df[y_fld]): df[y_fld] = df[y_fld].cat.codes
        y = df[y_fld].values
        skip_flds += [y_fld]
    df.drop(skip_flds, axis=1, inplace=True)

    if na_dict is None: na_dict = {}
    for n,c in df.items(): na_dict = fix_missing(df, c, n, na_dict)
    if do_scale: mapper = scale_vars(df, mapper)
    for n,c in df.items(): numericalize(df, c, n, max_n_cat)
    df = pd.get_dummies(df, dummy_na=True)
    df = pd.concat([ignored_flds, df], axis=1)
    res = [df, y, na_dict]
    if do_scale: res = res + [mapper]
    return res

    if is_numeric_dtype(col):
        if pd.isnull(col).sum() or (name in na_dict):
            df[name+'_na'] = pd.isnull(col)
            filler = na_dict[name] if name in na_dict else col.median()
            df[name] = col.fillna(filler)
            na_dict[name] = filler
    return na_dict

def fix_missing(df, col, name, na_dict):

    if is_numeric_dtype(col):
        if pd.isnull(col).sum() or (name in na_dict):
            df[name+'_na'] = pd.isnull(col)
            filler = na_dict[name] if name in na_dict else col.median()
            df[name] = col.fillna(filler)
            na_dict[name] = filler
    return na_dict

def numericalize(df, col, name, max_n_cat):
 
    if not is_numeric_dtype(col) and ( max_n_cat is None or col.nunique()>max_n_cat):
        df[name] = col.cat.codes+1

## Data Preparation für DL

In [132]:
from pandas.api.types import is_string_dtype, is_numeric_dtype
df_trn, y_trn, nas = proc_df(benutzergruppen_df, 'Clusternumber')

Build train and validation set

In [133]:
from sklearn.model_selection import train_test_split
x, x_val, y, y_val = train_test_split(df_trn, y_trn, test_size=0.33, random_state=42)

In [134]:
x = x.values
x_val = x_val.values
x

array([[45.0, 4, 1, ..., 11, 11, True],
       [38.0, 4, 1, ..., 11, 11, False],
       [23.0, 2, 1, ..., 11, 11, False],
       ...,
       [36.0, 4, 1, ..., 11, 11, False],
       [52.0, 4, 1, ..., 3, 5, False],
       [33.0, 4, 1, ..., 11, 11, False]], dtype=object)

In [98]:
y = y-1
y_val = y_val-1
y[1:10]

array([1, 3, 3, 3, 0, 0, 0, 3, 3])

In [99]:
x.shape, y.shape

((5855, 25), (5855,))

In [100]:
x_train = x.reshape(-1, df_trn.shape[1]).astype('float32')
y_train = y

In [101]:
x_val = x_val.reshape(-1, df_trn.shape[1]).astype('float32')
x_val=torch.from_numpy(x_val)

y_val = y_val.astype('long')
y_val=torch.from_numpy(y_val)

Put Data through DataLoader, so we can use batches

In [102]:
from torch.utils.data import Dataset, DataLoader
class Data(Dataset):
    def __init__(self):
        self.x=torch.from_numpy(x_train).type(torch.FloatTensor)
        self.y=torch.from_numpy(y_train).type(torch.LongTensor)
        self.len=self.x.shape[0]
    def __getitem__(self,index):      
        return self.x[index], self.y[index]
    def __len__(self):
        return self.len

In [103]:
data_set=Data()

In [104]:
trainloader=DataLoader(dataset=data_set,batch_size=32)

In [105]:
data_set.x

tensor([[45.,  4.,  1.,  ..., 11., 11.,  1.],
        [38.,  4.,  1.,  ..., 11., 11.,  0.],
        [23.,  2.,  1.,  ..., 11., 11.,  0.],
        ...,
        [36.,  4.,  1.,  ..., 11., 11.,  0.],
        [52.,  4.,  1.,  ...,  3.,  5.,  0.],
        [33.,  4.,  1.,  ..., 11., 11.,  0.]])

In [106]:
data_set.y[0:10]

tensor([0, 1, 3, 3, 3, 0, 0, 0, 3, 3])

In [107]:
data_set.x.shape, data_set.y.shape

(torch.Size([5855, 25]), torch.Size([5855]))

# Build Model and train it

He Initialisation

In [108]:
class Net(nn.Module):
    def __init__(self,in_size,n_hidden1,n_hidden2,out_size,p=0):

        super(Net,self).__init__()
        self.drop=nn.Dropout(p=p)
        self.linear1=nn.Linear(in_size,n_hidden1)
        nn.init.kaiming_uniform_(self.linear1.weight,nonlinearity='relu')
        self.linear2=nn.Linear(n_hidden1,n_hidden2)
        nn.init.kaiming_uniform_(self.linear1.weight,nonlinearity='relu')
        self.linear3=nn.Linear(n_hidden2,n_hidden2)
        nn.init.kaiming_uniform_(self.linear3.weight,nonlinearity='relu')
        self.linear4=nn.Linear(n_hidden2,out_size)
        
    def forward(self,x):
        x=F.relu(self.linear1(x))
        x=self.drop(x)
        x=F.relu(self.linear2(x))
        x=self.drop(x)
        x=F.relu(self.linear3(x))
        x=self.drop(x)
        x=self.linear4(x)
        return x

In [109]:
model=Net(25,50,5,4)
model_drop=Net(25,50,5,4,p=0.5)
model_drop

Net(
  (drop): Dropout(p=0.5)
  (linear1): Linear(in_features=25, out_features=50, bias=True)
  (linear2): Linear(in_features=50, out_features=5, bias=True)
  (linear3): Linear(in_features=5, out_features=5, bias=True)
  (linear4): Linear(in_features=5, out_features=4, bias=True)
)

In [110]:
model_drop.train()

Net(
  (drop): Dropout(p=0.5)
  (linear1): Linear(in_features=25, out_features=50, bias=True)
  (linear2): Linear(in_features=50, out_features=5, bias=True)
  (linear3): Linear(in_features=5, out_features=5, bias=True)
  (linear4): Linear(in_features=5, out_features=4, bias=True)
)

In [111]:
optimizer_ofit = torch.optim.Adam(model.parameters(), lr=0.0001)
optimizer_drop = torch.optim.Adam(model_drop.parameters(), lr=0.0001)
criterion = torch.nn.CrossEntropyLoss()

In [112]:
LOSS={}
LOSS['training data no dropout']=[]
LOSS['validation data no dropout']=[]
LOSS['training data dropout']=[]
LOSS['validation data dropout']=[]

In [113]:
n_epochs=1000

for epoch in range(n_epochs):
    for x, y in trainloader:
        #make a prediction for both models 
        yhat = model(data_set.x)
        yhat_drop = model_drop(data_set.x)
        #calculate the lossf or both models 
        loss = criterion(yhat, data_set.y)
        loss_drop = criterion(yhat_drop, data_set.y)

        #store the loss for  both the training and validation  data for both models 
        LOSS['training data no dropout'].append(loss.item())
        LOSS['training data dropout'].append(loss_drop.item())
        model_drop.eval()
        model_drop.train()

        #clear gradient 
        optimizer_ofit.zero_grad()
        optimizer_drop.zero_grad()
        #Backward pass: compute gradient of the loss with respect to all the learnable parameters
        loss.backward()
        loss_drop.backward()
        #the step function on an Optimizer makes an update to its parameters
        optimizer_ofit.step()
        optimizer_drop.step()
        
        print('epoch {}, loss {}'.format(epoch, loss.item()))

epoch 0, loss 1.5134676694869995
epoch 0, loss 1.4765454530715942
epoch 0, loss 1.4576032161712646
epoch 0, loss 1.433874249458313
epoch 0, loss 1.4025768041610718
epoch 0, loss 1.384642243385315
epoch 0, loss 1.3954850435256958
epoch 0, loss 1.4118616580963135
epoch 0, loss 1.4123897552490234
epoch 0, loss 1.4006388187408447
epoch 0, loss 1.3866840600967407
epoch 0, loss 1.3779590129852295
epoch 0, loss 1.3770153522491455
epoch 0, loss 1.3809250593185425
epoch 0, loss 1.3846732378005981
epoch 0, loss 1.3852630853652954
epoch 0, loss 1.382201075553894
epoch 0, loss 1.3764606714248657
epoch 0, loss 1.3701186180114746
epoch 0, loss 1.3657329082489014
epoch 0, loss 1.36436927318573
epoch 0, loss 1.3653687238693237
epoch 0, loss 1.3664207458496094
epoch 0, loss 1.3655314445495605
epoch 0, loss 1.3624211549758911
epoch 0, loss 1.3582528829574585
epoch 0, loss 1.3546836376190186
epoch 0, loss 1.3527686595916748
epoch 0, loss 1.3522710800170898
epoch 0, loss 1.352068543434143
epoch 0, loss 1.

epoch 1, loss 1.2450981140136719
epoch 1, loss 1.244741678237915
epoch 1, loss 1.2443809509277344
epoch 1, loss 1.2440173625946045
epoch 1, loss 1.2436556816101074
epoch 1, loss 1.2432864904403687
epoch 1, loss 1.2429145574569702
epoch 1, loss 1.242537021636963
epoch 1, loss 1.2421612739562988
epoch 1, loss 1.2417784929275513
epoch 1, loss 1.2413909435272217
epoch 1, loss 1.2410039901733398
epoch 1, loss 1.2406127452850342
epoch 1, loss 1.2402209043502808
epoch 1, loss 1.2398240566253662
epoch 1, loss 1.2394262552261353
epoch 1, loss 1.239025592803955
epoch 1, loss 1.2386218309402466
epoch 1, loss 1.2382103204727173
epoch 1, loss 1.2378010749816895
epoch 1, loss 1.2373958826065063
epoch 1, loss 1.236981987953186
epoch 1, loss 1.2365719079971313
epoch 1, loss 1.2361483573913574
epoch 1, loss 1.2357264757156372
epoch 1, loss 1.2352997064590454
epoch 1, loss 1.2348617315292358
epoch 1, loss 1.2344340085983276
epoch 1, loss 1.2339965105056763
epoch 1, loss 1.2335585355758667
epoch 1, loss 

epoch 2, loss 1.034454345703125
epoch 2, loss 1.0342870950698853
epoch 2, loss 1.0341262817382812
epoch 2, loss 1.0339564085006714
epoch 2, loss 1.0337986946105957
epoch 2, loss 1.0336329936981201
epoch 2, loss 1.0334672927856445
epoch 2, loss 1.0333095788955688
epoch 2, loss 1.0331450700759888
epoch 2, loss 1.0329922437667847
epoch 2, loss 1.0328364372253418
epoch 2, loss 1.032676100730896
epoch 2, loss 1.032528281211853
epoch 2, loss 1.0323742628097534
epoch 2, loss 1.0322357416152954
epoch 2, loss 1.032103419303894
epoch 2, loss 1.0319713354110718
epoch 2, loss 1.0318553447723389
epoch 2, loss 1.0317625999450684
epoch 2, loss 1.0316853523254395
epoch 2, loss 1.031679630279541
epoch 2, loss 1.0316647291183472
epoch 2, loss 1.0317109823226929
epoch 2, loss 1.031633734703064
epoch 2, loss 1.0315425395965576
epoch 2, loss 1.0311663150787354
epoch 2, loss 1.0307899713516235
epoch 2, loss 1.0304008722305298
epoch 2, loss 1.03016996383667
epoch 2, loss 1.0300909280776978
epoch 2, loss 1.03

epoch 4, loss 0.9999557733535767
epoch 4, loss 1.0002729892730713
epoch 4, loss 1.0008389949798584
epoch 4, loss 1.0010757446289062
epoch 4, loss 1.0008199214935303
epoch 4, loss 0.9996556639671326
epoch 4, loss 0.9984173774719238
epoch 4, loss 0.9976083636283875
epoch 4, loss 0.9976098537445068
epoch 4, loss 0.9980959892272949
epoch 4, loss 0.9983026385307312
epoch 4, loss 0.9979267120361328
epoch 4, loss 0.9971010684967041
epoch 4, loss 0.9964803457260132
epoch 4, loss 0.9964038729667664
epoch 4, loss 0.9966374635696411
epoch 4, loss 0.9966579079627991
epoch 4, loss 0.9962220788002014
epoch 4, loss 0.9956545233726501
epoch 4, loss 0.9953515529632568
epoch 4, loss 0.995341420173645
epoch 4, loss 0.9953866600990295
epoch 4, loss 0.9952054023742676
epoch 4, loss 0.9948435425758362
epoch 4, loss 0.994480550289154
epoch 4, loss 0.9942317008972168
epoch 4, loss 0.9941115379333496
epoch 4, loss 0.9940609931945801
epoch 4, loss 0.9939553737640381
epoch 4, loss 0.9937443137168884
epoch 4, los

epoch 5, loss 0.9703234434127808
epoch 5, loss 0.9703784584999084
epoch 5, loss 0.9704180955886841
epoch 5, loss 0.9703831076622009
epoch 5, loss 0.9702823758125305
epoch 5, loss 0.9700510501861572
epoch 5, loss 0.9697996973991394
epoch 5, loss 0.9695161581039429
epoch 5, loss 0.9692604541778564
epoch 5, loss 0.9690737128257751
epoch 5, loss 0.9689691066741943
epoch 5, loss 0.9689263105392456
epoch 5, loss 0.9689192771911621
epoch 5, loss 0.968941867351532
epoch 5, loss 0.9689177870750427
epoch 5, loss 0.9688889384269714
epoch 5, loss 0.9688500761985779
epoch 5, loss 0.9687703251838684
epoch 5, loss 0.9687342643737793
epoch 5, loss 0.968639612197876
epoch 5, loss 0.9685548543930054
epoch 5, loss 0.9684149026870728
epoch 5, loss 0.9683091044425964
epoch 5, loss 0.9682008624076843
epoch 5, loss 0.9681292772293091
epoch 5, loss 0.9680359959602356
epoch 5, loss 0.9679579734802246
epoch 5, loss 0.9678829908370972
epoch 5, loss 0.9678019881248474
epoch 5, loss 0.9677234888076782
epoch 5, los

...

epoch 494, loss 0.8368614315986633
epoch 494, loss 0.8368473649024963
epoch 494, loss 0.8370682597160339
epoch 494, loss 0.837627649307251
epoch 494, loss 0.838238537311554
epoch 494, loss 0.8391615152359009
epoch 494, loss 0.8398382663726807
epoch 494, loss 0.840977668762207
epoch 494, loss 0.8427070379257202
epoch 494, loss 0.8444461226463318
epoch 494, loss 0.8473441004753113
epoch 494, loss 0.8490400314331055
epoch 494, loss 0.851375937461853
epoch 494, loss 0.8511770367622375
epoch 494, loss 0.8515661954879761
epoch 494, loss 0.848722517490387
epoch 494, loss 0.8462433815002441
epoch 494, loss 0.842345118522644
epoch 494, loss 0.8393707871437073
epoch 494, loss 0.8375675678253174
epoch 494, loss 0.83686763048172
epoch 494, loss 0.8371816873550415
epoch 494, loss 0.8381726741790771
epoch 494, loss 0.8392099142074585
epoch 494, loss 0.8404675722122192
epoch 494, loss 0.8417408466339111
epoch 494, loss 0.8424221873283386
epoch 494, loss 0.8434913158416748
epoch 494, loss 0.8442472815

epoch 495, loss 0.8401333093643188
epoch 495, loss 0.8386011719703674
epoch 495, loss 0.8375855088233948
epoch 495, loss 0.8367184996604919
epoch 495, loss 0.8368526101112366
epoch 495, loss 0.8372249007225037
epoch 495, loss 0.8378052115440369
epoch 495, loss 0.8389049768447876
epoch 495, loss 0.8398427367210388
epoch 495, loss 0.84084552526474
epoch 495, loss 0.8423599600791931
epoch 495, loss 0.84425288438797
epoch 495, loss 0.8465626835823059
epoch 495, loss 0.8477197885513306
epoch 495, loss 0.8493826389312744
epoch 495, loss 0.8484703302383423
epoch 495, loss 0.8479030728340149
epoch 495, loss 0.844792366027832
epoch 495, loss 0.8415179252624512
epoch 495, loss 0.8394826650619507
epoch 495, loss 0.8380498886108398
epoch 495, loss 0.837221622467041
epoch 495, loss 0.8371022939682007
epoch 495, loss 0.8375276327133179
epoch 495, loss 0.8379805088043213
epoch 495, loss 0.838633120059967
epoch 495, loss 0.8400796055793762
epoch 495, loss 0.8408350944519043
epoch 495, loss 0.841721892

epoch 496, loss 0.8434690237045288
epoch 496, loss 0.8436400890350342
epoch 496, loss 0.8445740342140198
epoch 496, loss 0.8442731499671936
epoch 496, loss 0.8434393405914307
epoch 496, loss 0.8421308994293213
epoch 496, loss 0.8410943746566772
epoch 496, loss 0.8400430083274841
epoch 496, loss 0.83908611536026
epoch 496, loss 0.8386090993881226
epoch 496, loss 0.8379366397857666
epoch 496, loss 0.8373916149139404
epoch 496, loss 0.8369735479354858
epoch 496, loss 0.8369038105010986
epoch 496, loss 0.8369077444076538
epoch 496, loss 0.8371822834014893
epoch 496, loss 0.8373590707778931
epoch 496, loss 0.8378665447235107
epoch 496, loss 0.8386248350143433
epoch 496, loss 0.8393775820732117
epoch 497, loss 0.8405405879020691
epoch 497, loss 0.8416320085525513
epoch 497, loss 0.8437127470970154
epoch 497, loss 0.846551239490509
epoch 497, loss 0.8475906252861023
epoch 497, loss 0.8492457866668701
epoch 497, loss 0.8487054705619812
epoch 497, loss 0.8482890725135803
epoch 497, loss 0.84549

epoch 498, loss 0.8454912304878235
epoch 498, loss 0.84541916847229
epoch 498, loss 0.8462817072868347
epoch 498, loss 0.8451266288757324
epoch 498, loss 0.8444722890853882
epoch 498, loss 0.8424773216247559
epoch 498, loss 0.8410196900367737
epoch 498, loss 0.8398949503898621
epoch 498, loss 0.8385774493217468
epoch 498, loss 0.8379144072532654
epoch 498, loss 0.8370776176452637
epoch 498, loss 0.8369084000587463
epoch 498, loss 0.8366977572441101
epoch 498, loss 0.836756706237793
epoch 498, loss 0.8374362587928772
epoch 498, loss 0.8383801579475403
epoch 498, loss 0.8393759727478027
epoch 498, loss 0.8404854536056519
epoch 498, loss 0.8418204188346863
epoch 498, loss 0.8436791300773621
epoch 498, loss 0.844325602054596
epoch 498, loss 0.8459225296974182
epoch 498, loss 0.8461076021194458
epoch 498, loss 0.846484899520874
epoch 498, loss 0.8451780080795288
epoch 498, loss 0.8441321849822998
epoch 498, loss 0.8419659733772278
epoch 498, loss 0.8403088450431824
epoch 498, loss 0.8390587

epoch 499, loss 0.8412672281265259
epoch 499, loss 0.8434092998504639
epoch 499, loss 0.8446014523506165
epoch 499, loss 0.8464391827583313
epoch 499, loss 0.8464478254318237
epoch 499, loss 0.8476144075393677
epoch 499, loss 0.8465777635574341
epoch 499, loss 0.8455775380134583
epoch 499, loss 0.8432402610778809
epoch 499, loss 0.8411680459976196
epoch 499, loss 0.8391452431678772
epoch 499, loss 0.8376748561859131
epoch 499, loss 0.8367335796356201
epoch 499, loss 0.836831271648407
epoch 499, loss 0.8374581336975098
epoch 499, loss 0.8388565182685852
epoch 499, loss 0.8400696516036987
epoch 499, loss 0.8416374921798706
epoch 499, loss 0.8430218696594238
epoch 499, loss 0.8440305590629578
epoch 499, loss 0.8451369404792786
epoch 499, loss 0.8450775742530823
epoch 499, loss 0.8451696634292603
epoch 499, loss 0.8441154360771179
epoch 499, loss 0.8433711528778076
epoch 499, loss 0.8419897556304932
epoch 499, loss 0.8402807712554932
epoch 499, loss 0.8390708565711975
epoch 499, loss 0.838

In [114]:
yhat[0:10]

tensor([[ 0.7857,  0.0641, -0.1256, -0.2769],
        [ 0.6551,  0.8791, -0.4079, -0.2749],
        [-2.0033,  1.4733, -3.5871,  2.0436],
        [-1.0480, -0.3078, -3.1001,  1.8546],
        [ 0.5233, -1.8513, -1.6619,  0.9474],
        [-0.3768,  0.3282, -0.3747,  0.2067],
        [ 1.8179,  0.3564,  0.5076, -1.0116],
        [ 0.9333,  1.3803, -0.7700, -0.3174],
        [-2.8159, -0.3859, -4.8396,  3.3253],
        [ 0.1681, -1.0528, -1.5380,  0.8466]], grad_fn=<SliceBackward>)

In [115]:
torch.max(yhat.data,1)

(tensor([0.7857, 0.8791, 2.0436,  ..., 1.9490, 1.3053, 1.5600]),
 tensor([0, 1, 3,  ..., 3, 3, 3]))

In [116]:
y

tensor([1, 1, 0, 3, 2, 0, 3, 3, 0, 2, 1, 1, 0, 3, 0, 1, 1, 0, 3, 3, 3, 3, 3, 3,
        1, 3, 2, 0, 3, 1, 3])

In [117]:
z = model(x_val)
z_dropout = model_drop(x_val)

In [118]:
_,yhat=torch.max(z.data,1)
yhat[0:20]

tensor([3, 3, 3, 3, 0, 3, 3, 0, 0, 3, 0, 1, 3, 3, 0, 3, 3, 3, 0, 0])

In [119]:
_,yhat_dropout=torch.max(z_dropout.data,1)
yhat_dropout[0:20]

tensor([3, 3, 3, 0, 0, 3, 0, 0, 0, 3, 0, 0, 0, 0, 0, 3, 3, 3, 3, 0])

In [120]:
y_val[0:20]

tensor([3, 3, 0, 3, 2, 3, 1, 0, 3, 0, 0, 3, 2, 1, 1, 3, 3, 3, 0, 3])

In [121]:
# Making the Confusion Matrix
eval_matrix = (pd.crosstab(y_val, yhat))
print(eval_matrix)

col_0    0    1    3
row_0               
0      782  142  178
1      186  159  178
2      196   28   87
3      162  115  671


In [122]:
# Making the Confusion Matrix
eval_matrix_dropout = (pd.crosstab(y_val, yhat_dropout))
print(eval_matrix_dropout)

col_0    0    3
row_0          
0      932  170
1      314  209
2      241   70
3      353  595


In [125]:
(eval_matrix[0][0]+eval_matrix[3][3])/y_val.shape[0]

0.5038141470180305

In [126]:
(eval_matrix_dropout[0][0]+eval_matrix_dropout[3][3])/y_val.shape[0]

0.5294729542302358